In [3]:
# !pip install langchain openai chromadb tiktoken pypdf panel notebook

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 19.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.6/73.6 kB 10.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 123.6/123.6 kB 14.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 70.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 254.5/254.5 kB 23.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 90.0/90.0 kB 9.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.6/62.6 kB 7.5 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 965.1/965.1 kB 57.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.4/58.4 kB 6.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.3/5.3 MB 73.3 M

In [4]:
# !pip install tiktoken

In [5]:
import os
from langchain.chains import RetrievalQA
from langchain.llms import OpenAI
from langchain.document_loaders import TextLoader
from langchain.document_loaders import PyPDFLoader
from langchain.indexes import VectorstoreIndexCreator
from langchain.text_splitter import CharacterTextSplitter
from langchain.embeddings import OpenAIEmbeddings
from langchain.vectorstores import Chroma
from google.colab import drive
import panel as pn
import tempfile

In [6]:
pn.extension('texteditor', template="bootstrap", sizing_mode='stretch_width')
pn.state.template.param.update(
    main_max_width="690px",
    header_background="#F08080",
)

In [7]:
file_input = pn.widgets.FileInput(width=300)

openaikey = pn.widgets.PasswordInput(
    value="", placeholder="Enter your OpenAI API Key here...", width=300
)
prompt = pn.widgets.TextEditor(
    value="", placeholder="Enter your questions here...", height=160, toolbar=False
)
run_button = pn.widgets.Button(name="Run!")

select_k = pn.widgets.IntSlider(
    name="Number of relevant chunks", start=1, end=5, step=1, value=2
)
select_chain_type = pn.widgets.RadioButtonGroup(
    name='Chain type',
    options=['stuff', 'map_reduce', "refine", "map_rerank"]
)

widgets = pn.Row(
    pn.Column(prompt, run_button, margin=5),
    pn.Card(
        "Chain type:",
        pn.Column(select_chain_type, select_k),
        title="Advanced settings", margin=10
    ), width=600
)

In [8]:
file_input

FileInput(width=300)

In [9]:
file_input.value

b'%PDF-1.3\n%\xc4\xe5\xf2\xe5\xeb\xa7\xf3\xa0\xd0\xc4\xc6\n6 0 obj\n<< /Length 7 0 R /Filter /FlateDecode >>\nstream\nx\x01\xa4\xbd\xdb\xae#Kv\x9e{\xcf\xa7\xe0e\xad\x8b\xc9f\x1e\xc9\xbc\x94Z\xea\xf666\xbc-\xb9\x0c\xc10|\xe3\xb2Z\xcbF\x95\xda\xea\xb2a\xf8\xed\xf7\xf7\x8d\xc88\x90\x93+3\t\xa9\xa1U\x93Af\xe6\x88q\xf8\xc7!FD\xfe\xcb\xf9\xef\xce\xffr\xbe\xf2\xbf\xe96\x9fo\xb7\xf1\xfc\x97\x7f<\xff\xc3\xf9\x9f\xcf\xbf\xfb\xfd\xcf\xee\xfc\xed\xe7\xf9z\xb9\xf7\x8b\xff\xed:\xfe{\x1b\xbb\xf3\xcfo\xe7\xdf\xfd\x91/\xff\x89/\xebu\'\xae\xfb\xd3o\xde\xec\x8f?{\x7f\x9f\xaf\xfb\xdd\x1f~t\xe7\xbf\xf9s\xfc|\x9co\x97\xfb2\x9c\x87\xf1|\xeb/\xe3r?\x0f\xf7\xcb\xb5\xbby\xc3\x07B\xe2i\xcd\xc3\xd3\x85\xfd\xed<\xf5\x97i\xb9\x8f\xe7\x1f\xe7:\xc4-z\xee\xf8\xfd<\xde\xae\x97e\xb8\xdfN\xd3\xa7\xa1r\xa1\xbfZ.\xc3m\xae\xf7j\x87\xae\x97a\x9e\x1f\xef\xf5i\xe8<\xf6\x97~\x86}\xf5\x89\xe7a\xb9\xf4\x03t\x8d\xcc\xab\xbbrs&6t\xa3\x03\xd3e\x1c\xa62p\xfav\x1e\xef\xc3e\x18\x972\xe4}b\xc8\xcb\xe6\xcb\xf5\xde\xa5[\x8f\xfcy\x7f\x18\x

In [10]:
file_input.filename

'big-data-analytics-white-paper.pdf'

In [11]:
openaikey

PasswordInput(placeholder='Enter your OpenAI A..., width=300)

In [12]:
widgets

Big data is a large volume of data that is too large and complex for traditional data processing tools to manage. It is often made up of data from multiple sources that need to be analyzed to gain insights into trends and patterns. Big data analytics is the application of advanced analytic techniques to very big data sets. 
 Big data is a large volume of data that is too large and complex to be managed and analyzed with traditional data processing and storage tools. It is usually characterized by its size, variety, and velocity, and requires specialized tools and techniques for storage, analysis, and visualization. 
 Big data is large volumes of highly detailed data that can be used to discover facts that were previously unknown. It is often accompanied by advanced analytics to help uncover new insights. 
 Big data is large volumes of highly detailed data that can be used to discover facts not previously known. It is often used to track customer behavior and other aspects of business operations. 
 Big data is large volumes of data that can be used to discover facts that were not previously known. It includes data from sensors, devices, third parties, Web applications, and social media, and it can be used with advanced analytics to gain insights.

Row(width=600)
    [0] Column(margin=5, sizing_mode='stretch_width')
        [0] TextEditor(height=160, placeholder='Enter your questions h..., sizing_mode='stretch_width', toolbar=False)
        [1] Button(name='Run!', sizing_mode='stretch_width')
    [1] Card(margin=10, sizing_mode='stretch_width', title='Advanced settings')
        [0] Markdown(str, sizing_mode='stretch_width')
        [1] Column(sizing_mode='stretch_width')
            [0] RadioButtonGroup(name='Chain type', options=['stuff', 'map_reduce', ...], sizing_mode='stretch_width', value='stuff')
            [1] IntSlider(end=5, name='Number of relevant c..., sizing_mode='stretch_width', start=1, value=2)

In [18]:
def qa(file, query, chain_type, k):
    # load document
    loader = PyPDFLoader(file)
    documents = loader.load()
    # split the documents into chunks
    text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=0)
    texts = text_splitter.split_documents(documents)
    # select which embeddings we want to use
    embeddings = OpenAIEmbeddings()
    # create the vectorestore to use as the index
    db = Chroma.from_documents(texts, embeddings)
    # expose this index in a retriever interface
    retriever = db.as_retriever(search_type="similarity", search_kwargs={"k": k})
    # create a chain to answer questions
    qa = RetrievalQA.from_chain_type(
        llm=OpenAI(), chain_type=chain_type, retriever=retriever, return_source_documents=True)
    result = qa({"query": query})
    print(result['result'])
    return result

In [19]:
os.environ["OPENAI_AI_KEY"] = ""

In [20]:
convos = []  # store all panel objects in a list

def qa_result(_):
    os.environ["OPENAI_API_KEY"] = openaikey.value

    # save pdf file to a temp file
    if file_input.value is not None:
        file_input.save("/content/temp.pdf")

        prompt_text = prompt.value
        if prompt_text:
            result = qa(file="/content/temp.pdf", query=prompt_text, chain_type=select_chain_type.value, k=select_k.value)
            convos.extend([
                pn.Row(
                    pn.panel("\U0001F60A", width=10),
                    prompt_text,
                    width=600
                ),
                pn.Row(
                    pn.panel("\U0001F916", width=10),
                    pn.Column(
                        result["result"],
                        "Relevant source text:",
                        pn.pane.Markdown('\n--------------------------------------------------------------------\n'.join(doc.page_content for doc in result["source_documents"]))
                    )
                )
            ])
            #return convos
    return pn.Column(*convos, margin=15, width=575, min_height=400)

In [21]:
qa_interactive = pn.panel(
    pn.bind(qa_result, run_button),
    loading_indicator=True,
)

 Big data refers to large volumes of highly detailed data that can be used to discover facts that were previously unknown. It is often used with advanced analytics to track customer behavior, understand the current state of a business, and uncover new insights.


In [22]:
output = pn.WidgetBox('*Output will show up here:*', qa_interactive, width=630, scroll=True)

In [23]:
# layout
pn.Column(
    pn.pane.Markdown("""
    ## \U0001F60A! Question Answering with your PDF file

    1) Upload a PDF. 2) Enter OpenAI API key. This costs $. Set up billing at [OpenAI](https://platform.openai.com/account). 3) Type a question and click "Run".

    """),
    pn.Row(file_input,openaikey),
    output,
    widgets

).servable()

Manfaat big data analytics termasuk lebih tepat dalam pemasaran yang ditargetkan oleh influencer sosial (61%), segmentasi basis pelanggan (41%), dan mengenali kesempatan-kesempatan pasar dan penjualan (38%). Big data analytics juga dapat membantu mengembangkan definisi untuk churn dan perilaku pelanggan lainnya (35%), serta memahami perilaku pelanggan dari aliran klik (27%). Ini juga dapat memberikan lebih banyak dan akurat insight bisnis (45%), memahami perubahan bisnis (30%), perencanaan dan peramalan yang lebih baik (29%), dan mengidentifikasi penyebab utama biaya (29%). Aplikasi analitik khusus juga dapat memanfaatkan big data analytics, seperti deteksi penipuan (33%), kuantifikasi risiko (30%), dan sentimen pasar yang berkembang 
 Big data dapat membantu untuk mengembangkan definisi dari churn dan perilaku pelanggan lainnya (35%), serta sebuah pemahaman perilaku konsumen dari clickstreams (27%). Big data juga dapat membantu untuk menghasilkan lebih banyak dan akurat wawasan bisnis (45%), pemahaman tentang perubahan bisnis (30%), perencanaan dan peramalan yang lebih baik (29%), dan identifikasi akar dari biaya (29%). Big data juga dapat membantu untuk menargetkan pemasaran sosial-influencer yang lebih baik (61%), segmentasi basis pelanggan (41%), dan pengenalan peluang pasar dan penjualan (38%). Selain itu, big data juga dapat membantu untuk mendeteksi penipuan (33%), kuantifikasi risiko (30%), dan tren sentimen pasar (30%). Big data juga

Column(sizing_mode='stretch_width')
    [0] Markdown(str, sizing_mode='stretch_width')
    [1] Row(sizing_mode='stretch_width')
        [0] FileInput(filename='big-data-analytics-white-..., mime_type='application/pdf', value=b'%PDF-1.3\n%\xc4\xe5\xf2\..., width=300)
        [1] PasswordInput(placeholder='Enter your OpenAI A..., value='sk-3kvONAwOrrX8bSlFWfqDT3..., value_input='sk-3kvONAwOrrX8bSlFWfqDT3..., width=300)
    [2] WidgetBox(scroll=True, width=630)
        [0] Markdown(str, sizing_mode='stretch_width')
        [1] ParamFunction(function, _pane=Column, loading_indicator=True, sizing_mode='stretch_width')
    [3] Row(width=600)
        [0] Column(margin=5, sizing_mode='stretch_width')
            [0] TextEditor(height=160, placeholder='Enter your questions h..., sizing_mode='stretch_width', toolbar=False, value='<p>apa itu big data</p>')
            [1] Button(clicks=6, name='Run!', sizing_mode='stretch_width')
        [1] Card(margin=10, sizing_mode='stretch_width', title='Advanced settings')
            [0] Markdown(str, sizing_mode='stretch_width')
            [1] Column(sizing_mode='stretch_width')
                [0] RadioButtonGroup(name='Chain type', options=['stuff', 'map_reduce', ...], sizing_mode='stretch_width', value='stuff')
                [1] IntSlider(end=5, name='Number of relevant c..., sizing_mode='stretch_width', start=1, value=2)